# Load in spectra

In [1]:
# The sys.stdout statements is to resolve proplems with printing statements in jupyter notebook, 
# when removed progress updates printed are not shown in the notebookr
import sys
stdout = sys.stdout

from ms2query.ms2library import MS2Library
sys.stdout = stdout

tanimoto_scores_df_file = "../../../downloads/gnps_210409/ALL_GNPS_210409_positive_tanimoto_scores.pickle"
sqlite_file =  "../../../downloads/gnps_210409/spectra/ALL_GNPS_210409_train_split.sqlite"
classifiers_file = "../../../downloads/Case_studies/ALL_GNPS_210409_positive_processed_annotated_CF_NPC_classes.txt"

# Models
s2v_model_file = "../../../downloads/gnps_210409/models/ALL_GNPS_210409_Spec2Vec_ms2query.model"
ms2ds_model_file = "../../../downloads/gnps_210409/models/ms2ds_20210420-141937_data210409_10k_500_500_200.hdf5"
ms2query_model = "../../../downloads/gnps_210409/train_ms2query_model/ms2query_model_all_scores_dropout_regularization.hdf5"

# Embeddings
s2v_embeddings_file =  "../../../downloads/gnps_210409/embeddings/s2v_embeddings_train_spectra_210426.pickle"
ms2ds_embeddings_file =  "../../../downloads/gnps_210409/embeddings/ms2ds_embeddings_train_spectra_210426.pickle"

Create library object

In [2]:
ms2library = MS2Library(sqlite_file, s2v_model_file, ms2ds_model_file, s2v_embeddings_file, ms2ds_embeddings_file)

In [3]:
import os
from matchms.importing.load_from_mzml import load_from_mzml
import pickle
from ms2query.utils import add_classifiers_to_df
from ms2query.query_from_sqlite_database import get_metadata_from_sqlite

def store_result_analog_search_and_library_search(library_object, dirname, file):
    spectra = list(load_from_mzml(os.path.join(dirname, file)))
    assert os.path.exists(os.path.join(dirname, "results"))
    
    # set charge to 1, if charge is not set, the parent mass cannot be derived
    spectra = [spectrum.set('charge', 1) for spectrum in spectra]
    
    library_matches = get_results_library_search(library_object, spectra)
    library_search_results_file = os.path.join(dirname, "results", file[:-5]+"_results_library_search.pickle")
    pickle.dump(library_matches, open(library_search_results_file, "wb"))
    
    analog_results = get_results_analog_search(library_object, spectra)
    analog_results_file = os.path.join(dirname, "results", file[:-5]+"_results_analog_search.pickle")
    pickle.dump(analog_results, open(analog_results_file, "wb"))
    
    
def get_results_library_search(library_object, spectra):
    library_matches = library_object.select_potential_true_matches(spectra)
    
    library_matches_with_extra_info = []
    for matches_df in library_matches:
        metadata_list = list(get_metadata_from_sqlite(sqlite_file,
                                       list(matches_df.index)).values())
        compound_names = [metadata["compound_name"] for metadata in metadata_list]
        matches_df["compound_name"] = compound_names
        inchikeys = [metadata["inchikey"][:14] for metadata in metadata_list]
        matches_df["inchikey"] = inchikeys
        matches_df = add_classifiers_to_df(classifiers_file,
                                                 matches_df)
        matches_df.set_index("spectrum_id", inplace=True)
        library_matches_with_extra_info.append(matches_df)
    return library_matches_with_extra_info

def get_results_analog_search(library_object, spectra):
    results_analog_search = library_object.analog_search(spectra, ms2query_model)
    results_list = []
    for result_table in results_analog_search:
        df_with_results = result_table.create_dataframe_with_compound_classification(                              
            20,
            classifiers_file,
            add_selection=["inchikey", "smiles", "spectrum_ids", "compound_name", 
                           "ms2query_model_prediction", "cf_kingdom",
                           "cf_superclass", "cf_class", "cf_subclass",
                           "cf_direct_parent", "npc_class_results",
                           "npc_superclass_results", "npc_pathway_results"])
        results_list.append(df_with_results)
    return results_list

In [4]:
import os
dirname = "../../../downloads/Case_studies/Robert_jansen"

for file in os.listdir(dirname):
    if file.endswith(".mzML"):
        store_result_analog_search_and_library_search(ms2library, dirname, file)

../../../downloads/Case_studies/Robert_jansen\Brocadia-Excl1-POS-1.mzML
../../../downloads/Case_studies/Robert_jansen\results\Brocadia-Excl1-POS-1_results_analog_search.pickle


Selecting potential perfect matches:   0%|                                                                                                                               | 0/1028 [00:00<?, ?it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.95%.


Selecting potential perfect matches:   0%|▍                                                                                                                      | 4/1028 [00:05<16:40,  1.02it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.54%.


...

Found 2 word(s) missing in the model. Weighted missing percentage not covered by the given model is 1.41%.


collecting matches info: 691it [07:35,  1.85it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.87%.


collecting matches info: 692it [07:36,  1.52it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.69%.


In [5]:
import os
dirname = "../../../downloads/Case_studies/Berries"

for file in os.listdir(dirname):
    if file.endswith("POS.mzML"):
        store_result_analog_search_and_library_search(ms2library, dirname, file)

Selecting potential perfect matches:   0%|                                                                                                                       | 1/1014 [00:00<13:09,  1.28it/s]

Found 8 word(s) missing in the model. Weighted missing percentage not covered by the given model is 4.08%.


Selecting potential perfect matches:   0%|▍                                                                                                                      | 4/1014 [00:02<11:21,  1.48it/s]

Found 8 word(s) missing in the model. Weighted missing percentage not covered by the given model is 4.10%.


Selecting potential perfect matches:   1%|▊                                                                                                                      | 7/1014 [00:04<11:01,  1.52it/s]

...

collecting matches info: 900it [10:54,  1.23it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.81%.


collecting matches info: 902it [10:55,  1.47it/s]

Found 1 word(s) missing in the model. Weighted missing percentage not covered by the given model is 0.79%.


collecting matches info: 903it [10:56,  1.38it/s]
